In [1]:
import itertools
import pandas as pd
import numpy as np
import toytree
import toyplot
import arviz as az
import pymc3 as pm

### Tree and dataframe setup

In [2]:
# generate a random tree
NSPECIES = 80
TREE = toytree.rtree.bdtree(
    ntips=NSPECIES,
    seed=666,
).mod.node_scale_root_height(1.0)

# node idxs that delimit several distinct clades on this tree
CLADES = [152, 153, 154, 155]

# draw and color the four major clades
TREE.draw(
    layout='d', 
    width=500,
    tip_labels=False,
    edge_colors=TREE.get_edge_values_mapped({
        j: toytree.colors[i] for i, j in enumerate(CLADES)
    }),
    scalebar=True,
);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="tc606e8688a494c838616bb8a361db0b6" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> 0.0 0.5 1.0

In [3]:
# make group index (gidx)
crown_dict = {i: TREE.get_tip_labels(i) for i in CLADES}
gidx = np.zeros(TREE.ntips, dtype=int)
for tidx, tip in enumerate(TREE.get_tip_labels()):
    for cidx, clade in enumerate(crown_dict):
        if tip in crown_dict[clade]:
            gidx[tidx] = cidx
gidx

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
       3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3])

In [4]:
# True param values
𝛼_mean = 0.05
𝛼_std = 0.02
𝛽_mean = 3.0
𝛽_std = 0.2
𝜓_mean = 0.0
𝜓_std = 0.33

# 4 different clade effects on rate of RI (used for partial-pooling data)
𝜓_0_mean = 1.0
𝜓_0_std = 0.1
𝜓_1_mean = 0.5
𝜓_1_std = 0.05
𝜓_2_mean = -0.5
𝜓_2_std = 0.05
𝜓_3_mean = -1.0
𝜓_3_std = 0.1

In [5]:
# species dataframe
SPECIES_DATA = pd.DataFrame({
    "gidx": gidx,
    "b": np.random.normal(𝛽_mean, 𝛽_std, TREE.ntips),
    "psi": np.random.normal(𝜓_mean, 𝜓_std, TREE.ntips),
    "psi_x": np.concatenate([
        np.random.normal(𝜓_0_mean, 𝜓_0_std, len(gidx[gidx == 0])),
        np.random.normal(𝜓_1_mean, 𝜓_1_std, len(gidx[gidx == 1])),
        np.random.normal(𝜓_2_mean, 𝜓_2_std, len(gidx[gidx == 2])),
        np.random.normal(𝜓_3_mean, 𝜓_3_std, len(gidx[gidx == 3])),
    ]),
})
SPECIES_DATA.head()

gidx         b       psi     psi_x
0     0  2.570468 -0.236524  0.997529
1     0  3.292698 -0.624017  0.863576
2     0  2.936227 -0.612795  0.956139
3     0  2.746916 -0.234236  1.115301
4     0  2.767121  0.031270  0.981499

### Generate crossing data

In [6]:
def get_dist(tree, idx0, idx1):
    "returns the genetic distance between two nodes on a tree"
    dist = tree.treenode.get_distance(
        tree.idx_dict[idx0], 
        tree.idx_dict[idx1],
    )
    return dist

# get all combinations of two sampled taxa
a, b = zip(*itertools.combinations(range(NSPECIES), 2))

# organize into DF and get genetic distance between pairs
DATA = pd.DataFrame({
    "sidx0": a,
    "sidx1": b,
    "dist": [get_dist(TREE, i, j) / 2 for (i, j) in zip(a, b)],
})

# get pairwise velocity
DATA['b'] = (
    np.random.normal(𝛽_mean, 𝛽_std, DATA.shape[0])
)

DATA['velo'] = (
    DATA['b']
    + SPECIES_DATA['psi'][DATA.sidx0].values
    + SPECIES_DATA['psi'][DATA.sidx1].values
)

DATA['velo_x'] = (
    DATA['b']
    + SPECIES_DATA['psi_x'][DATA.sidx0].values
    + SPECIES_DATA['psi_x'][DATA.sidx1].values
)

DATA['intercept'] = np.random.normal(𝛼_mean, 𝛼_std, DATA.shape[0])

# get logits
DATA['logit_b'] = (
    1 / (1 + np.exp(-(DATA.intercept + DATA.dist * DATA.b)))
)
DATA['logit'] = (
    1 / (1 + np.exp(-(DATA.intercept + DATA.dist * DATA.velo)))
)
DATA['logit_x'] = (
    1 / (1 + np.exp(-(DATA.intercept + DATA.dist * DATA.velo_x)))
)

# get RI estimates
DATA['RI_pooled'] = np.random.binomial(n=1, p=DATA.logit_b / DATA.logit_b.max())
DATA['RI_unpooled'] = np.random.binomial(n=1, p=DATA.logit / DATA.logit.max())
DATA['RI_partpooled'] = np.random.binomial(n=1, p=DATA.logit_x / DATA.logit_x.max())

DATA.head()

sidx0  sidx1      dist         b      velo    velo_x  intercept   logit_b  \
0      0      1  0.073376  2.881579  2.021039  4.742684   0.023752  0.558528   
1      0      2  0.089748  2.638508  1.789189  4.592176   0.074466  0.577194   
2      0      3  0.129770  3.113867  2.643107  5.226697   0.055129  0.612828   
3      0      4  0.144542  3.059197  2.853944  5.038226   0.059521  0.622860   
4      0      5  0.144542  2.620887  2.866354  4.699434   0.059066  0.607757   

      logit   logit_x  RI_pooled  RI_unpooled  RI_partpooled  
0  0.542906  0.591882          0            0              0  
1  0.558491  0.619306          1            1              0  
2  0.598237  0.675551          0            1              1  
3  0.615866  0.687350          1            1              1  
4  0.616182  0.676631          0            0              1

In [8]:
NSAMPLES = 2000
SAMPLE = DATA.sample(NSAMPLES).copy().reset_index(drop=True)
SAMPLE.head()

sidx0  sidx1      dist         b      velo    velo_x  intercept   logit_b  \
0     60     63  0.578689  2.921440  2.625589  1.913308   0.044766  0.850098   
1     46     74  0.592720  3.287330  3.246154  1.886728   0.043472  0.879948   
2     23     30  0.438896  2.615066  2.010742  4.803178   0.057368  0.769433   
3     61     71  0.592720  3.160457  2.911351  1.778620   0.020785  0.869217   
4     23     34  0.590047  3.069562  2.832857  4.990309   0.039344  0.864189   

      logit   logit_x  RI_pooled  RI_unpooled  RI_partpooled  
0  0.826950  0.759872          1            1              1  
1  0.877346  0.761655          1            0              0  
2  0.719074  0.897105          1            0              1  
3  0.851498  0.745548          1            1              1  
4  0.846948  0.951840          1            1              1

### Visualize data

In [9]:
def logit_plot(dist, logit, RI):
    canvas = toyplot.Canvas(width=500, height=250)
    ax0 = canvas.cartesian(
        label="pooled data (function)",
        xlabel="Genetic dist.",
        ylabel="Logit function",
        grid=(1, 2, 0),
    )
    ax1 = canvas.cartesian(
        label="pooled data (observation)",
        xlabel="Genetic dist.",
        ylabel="RI",
        grid=(1, 2, 1),
    )

    # points are jittered on x-axis for visibility
    ax0.scatterplot(
        dist,
        logit,
        size=5,
        opacity=0.33,
        color=toyplot.color.Palette()[0],
    );
    ax1.scatterplot(
        dist,
        RI,
        size=10,
        opacity=0.2,
        marker="|",
        mstyle={
            "stroke": toyplot.color.Palette()[1],
            "stroke-width": 3,
        },
    );
    return canvas, (ax0, ax1)

In [10]:
logit_plot(SAMPLE.dist, SAMPLE.logit_b, SAMPLE.RI_pooled);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="td7083bd63a604509bc3e3ffc2bd2e734" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <g class="toy

In [11]:
logit_plot(SAMPLE.dist, SAMPLE.logit, SAMPLE.RI_unpooled);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="t62e49530e9ed4d3f921823fa80eb39fd" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <c

In [12]:
logit_plot(SAMPLE.dist, SAMPLE.logit_x, SAMPLE.RI_partpooled);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="tdfe4d9a9c08b4a83ae6f50419135356a" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 250.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <circ

### Define models

In [13]:
def pooled_logistic(x, y, **kwargs):
    
    # define model
    with pm.Model() as model:  

        # parameters and error
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        
        # link function
        effect = 𝛼 + 𝛽 * x
        logit = pm.Deterministic("logit", pm.invlogit(effect))
        
        # data likelihood
        y = pm.Bernoulli("y", p=logit, observed=y)
        
        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]
    
        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

In [14]:
def unpooled_logistic(x, y, idx0, idx1, **kwargs):
    
    # define model
    with pm.Model() as model:
        
        # indexers
        sidx0 = pm.Data("spp_idx0", idx0.values)
        sidx1 = pm.Data("spp_idx1", idx1.values)

        # parameters and error
        𝜓_mean = pm.Normal('𝜓_mean', mu=0., sigma=5., shape=1)
        𝜓_std = pm.HalfNormal('𝜓_std', 5., shape=1)
        𝜓_offset = pm.Normal('𝜓_offset', mu=0, sigma=1., shape=TREE.ntips)
        𝜓 = pm.Deterministic('𝜓', 𝜓_mean + 𝜓_std * 𝜓_offset)
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        
        # link function
        effect = 𝛼 + (𝛽 + 𝜓[sidx0] + 𝜓[sidx1]) * x
        logit = pm.Deterministic("logit", pm.invlogit(effect))
        
        # data likelihood
        y = pm.Bernoulli("y", p=logit, observed=y)
        
        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]
    
        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

In [15]:
def partpooled_logistic(x, y, idx0, idx1, gidx, **kwargs):
    
    # define model
    with pm.Model() as model:
        
        # indexers
        sidx0 = pm.Data("spp_idx0", idx0)
        sidx1 = pm.Data("spp_idx1", idx1)
        gidx = pm.Data("gidx", gidx)

        # parameters and error
        𝜓_mean = pm.Normal('𝜓_mean', mu=0., sigma=5., shape=4)
        𝜓_std = pm.HalfNormal('𝜓_std', 5., shape=4)
        𝜓_offset = pm.Normal('𝜓_offset', mu=0, sigma=1., shape=TREE.ntips)
        𝜓 = pm.Deterministic('𝜓', 𝜓_mean[gidx] + 𝜓_std[gidx] * 𝜓_offset)
        𝛽 = pm.Normal('𝛽', mu=0., sigma=10., shape=1)
        𝛼 = pm.Normal('𝛼', mu=0., sigma=10., shape=1)
        
        # linear model prediction
        effect = 𝛼 + (𝛽 + 𝜓[sidx0] + 𝜓[sidx1]) * x
        logit = pm.Deterministic("logit", pm.invlogit(effect))
        
        # data likelihood (normal distributed errors)
        y = pm.Bernoulli("y", p=logit, observed=y)

        # sample posterior, skip burnin
        trace = pm.sample(**kwargs)[1000:]

        # show summary table
        stats = pm.summary(trace)
        
    # organize results
    result_dict = {
        'model': model, 
        'trace': trace,
        'stats': stats,
    }
    return result_dict

### Functions to plot results

In [16]:
def toytrace(trace, var_names, titles):
    """
    Plot posterior trace with toyplot
    """
    nvars = len(var_names)
    
    # setup canvase
    canvas = toyplot.Canvas(width=500, height=200 * nvars)
    
    # store axes
    axes = []
    
    # iter over params
    for pidx, param in enumerate(var_names):
        
        # get param posterior
        posterior = trace.get_values(param)
        
        # setup axes 
        ax = canvas.cartesian(grid=(nvars, 1, pidx))
        ax.y.show = False
        ax.x.spine.style = {"stroke-width": 1.5}
        ax.x.ticks.labels.style = {"font-size": "12px"}
        ax.x.ticks.show = True
        ax.x.label.text = f"param='{titles[pidx]}'"        
        
        # iterate over shape of param
        for idx in range(posterior.shape[1]):
            mags, bins = np.histogram(posterior[:, idx], bins=100)
            ax.plot(bins[1:], mags, stroke_width=2, opacity=0.6)
        axes.append(ax)
    return canvas, axes

In [17]:
import scipy.stats as stats

def draw_velocity_dists(trace, baseline=0.15):
    """
    Draw the clade velocities as gaussians
    """
    canvas = toyplot.Canvas(width=350, height=300)
    axes = canvas.cartesian(xlabel="Relative velocity of reproductive isolation")
    marks = []
    base = 0
    for i in range(trace['𝜓_mean'].shape[1]):
        
        loc = trace['𝜓_mean'][:, i].mean()
        scale = trace['𝜓_std'][:, i].mean()
        interval = stats.norm.interval(0.995, loc, scale)
        points = np.linspace(interval[0], interval[1], 100)
        mark = axes.fill(
            points, 
            stats.norm.pdf(points, loc=loc, scale=scale), 
            style={
                "fill-opacity": 0.45,
                "stroke": 'black',
                "stroke-opacity": 1.0,
                "stroke-width": 1,
            },
            baseline=np.repeat(base, 100),
        )
        marks.append(mark)
        axes.hlines(base, style={"stroke-dasharray": "5,5", 'stroke-width': 1})
        base += baseline
        
    axes.y.show = False
    axes.x.ticks.locator = toyplot.locator.Extended(only_inside=True)
    axes.x.ticks.show = True
    return canvas, axes, marks

In [18]:
# MCMC sampler kwargs
sample_kwargs = dict(
    tune=10000,
    draws=10000,
    target_accept=0.99,
    return_inferencedata=False,
    progressbar=True,
)

### Run three datasets under pooled model

In [19]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
pooled_model_pooled_data = pooled_logistic(*model_args[:2], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 366 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [ ]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
pooled_model_unpooled_data = pooled_logistic(*model_args[:2], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼]


In [27]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# pooled model
pooled_model_partpooled_data = pooled_logistic(*model_args[:2], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 336 seconds.
The number of effective samples is smaller than 25% for some parameters.


### Run three datasets under unpooled model

In [ ]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
unpooled_model_pooled_data = unpooled_logistic(*model_args[:4], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼, 𝜓_offset, 𝜓_std, 𝜓_mean]


In [32]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
unpooled_model_unpooled_data  = unpooled_logistic(*model_args[:4], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 23327 seconds.


In [34]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
unpooled_model_partpooled_data = unpooled_logistic(*model_args[:4], **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛽, 𝛼, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 15717 seconds.


### Run three datasets under partpooled model

In [36]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_pooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
partpooled_model_pooled_data = partpooled_logistic(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 8392 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [37]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_unpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
partpooled_model_unpooled_data = partpooled_logistic(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 11379 seconds.


In [20]:
# model input
model_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

# unpooled model
partpooled_model_partpooled_data = partpooled_logistic(*model_args, **sample_kwargs)

Auto-assigning NUTS sampler...
Initializing NUTS using jitter+adapt_diag...
Multiprocess sampling (4 chains in 4 jobs)
NUTS: [𝛼, 𝛽, 𝜓_offset, 𝜓_std, 𝜓_mean]


Sampling 4 chains for 10_000 tune and 10_000 draw iterations (40_000 + 40_000 draws total) took 10763 seconds.
The number of effective samples is smaller than 25% for some parameters.


In [21]:
partpooled_model_partpooled_data['stats']

mean     sd  hdi_3%  hdi_97%  mcse_mean  mcse_sd  ess_mean  \
𝜓_mean[0]    1.442  2.255  -2.913    5.542      0.030    0.021    5685.0   
𝜓_mean[1]    0.988  2.290  -3.367    5.209      0.030    0.021    5732.0   
𝜓_mean[2]   -0.203  2.255  -4.440    3.994      0.030    0.021    5709.0   
𝜓_mean[3]   -0.927  2.256  -5.215    3.242      0.030    0.021    5666.0   
𝜓_offset[0]  0.201  0.960  -1.598    2.013      0.005    0.005   39610.0   
...            ...    ...     ...      ...        ...      ...       ...   
logit[1995]  0.931  0.018   0.897    0.964      0.000    0.000   37812.0   
logit[1996]  0.830  0.030   0.775    0.888      0.000    0.000   30454.0   
logit[1997]  0.737  0.063   0.617    0.856      0.000    0.000   48048.0   
logit[1998]  0.749  0.061   0.632    0.865      0.000    0.000   43557.0   
logit[1999]  0.974  0.014   0.949    0.997      0.000    0.000   27134.0   

              ess_sd  ess_bulk  ess_tail  r_hat  
𝜓_mean[0]     5685.0    5685.0   10857.0    1.0  
𝜓_mean[1]     5732.0    5732.0   11323.0    1.0  
𝜓_mean[2]     5709.0    5710.0   10805.0    1.0  
𝜓_mean[3]     5666.0    5666.0   11267.0    1.0  
𝜓_offset[0]  18230.0   39590.0   27352.0    1.0  
...              ...       ...       ...    ...  
logit[1995]  37812.0   38848.0   29989.0    1.0  
logit[1996]  30333.0   30615.0   29121.0    1.0  
logit[1997]  48048.0   48240.0   32232.0    1.0  
logit[1998]  43252.0   43160.0   30963.0    1.0  
logit[1999]  27087.0   26540.0   30715.0    1.0  

[2170 rows x 11 columns]

In [22]:
toytrace(partpooled_model_partpooled_data['trace'], ['𝜓_mean', '𝜓_offset', '𝜓'], ['psi-mean', 'psi-offset', 'psi-spp']);

<svg class="toyplot-canvas-Canvas" height="600.0px" id="tc079ba5d81304c709ac6afd3155a3b82" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 500.0 600.0" width="500.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <path d="M 87.69644970263951 149.8469778117827 L 91.35608152382494 150.0 L 95.01571334501043 150.0 L 98.67534516619588 150.0 L 102.33497698738134 149.92348890589136 L 105.9946088085668 149.8469778117827 L 109.65424062975227 150.0 L 113.31387245093774 149.8469778117827 L 116.97350427212318 149.77046671767405 L 120.63313609330862 150.0 L 124.2927679144941 149.54093343534814 L 127.95239973567956 149.46442234123947 L 131.61203155686502 149.69395562356542 L 135.27166337805048 149.0053557765876 L 138.93129519923593 149.08186687069625 L 142.5909270204214 148.46977811782708 L 146.25055884160687 148.69931140015302 L 149.91019066279233 148.1637337413925 L 153.5698224839778 147.09257842387143 L 157.22945430516324 146.4804896710023 L 160.8890861263487 147.39862280030604 L 164.54871794753416 146.71002295332823 L 168.20834976871961 144.03213465952564 L 171.86798158990507 144.33817903596022 L 175.52761341109056 140.8186687069625 L 179.18724523227598 138.67635807192042 L 182.8468770534615 136.68706962509563 L 186.50650887464693 133.2440703902066 L 190.16614069583238 133.32058148431523 L 193.82577251701784 130.64269319051263 L 197.4854043382033 128.72991583779648 L 201.14503615938875 124.67482785003824 L 204.8046679805742 118.47742922723795 L 208.46429980175967 115.1874521805662 L 212.12393162294515 111.13236419280797 L 215.7835634441306 107.99540933435347 L 219.44319526531606 99.96174445294568 L 223.10282708650152 96.67176740627391 L 226.76245890768698 93.3052792654935 L 230.42209072887246 86.26625860749809 L 234.08172255005792 87.64345830145372 L 237.74135437124335 81.67559296097934 L 241.40098619242883 74.56006120887528 L 245.06061801361432 74.10099464422342 L 248.72024983479974 66.75592960979343 L 252.3798816559852 63.5424636572303 L 256.03951347717066 64.69013006885999 L 259.69914529835614 57.957153787299156 L 263.35877711954157 58.64575363427696 L 267.01840894072706 56.3504208110176 L 270.67804076191254 63.159908186687076 L 274.3376725830979 54.896710022953336 L 277.9973044042834 53.44299923488905 L 281.6569362254689 62.47130833970925 L 285.3165680466543 59.79342004590665 L 288.9761998678398 64.00153022188218 L 292.6358316890253 68.51568477429228 L 296.29546351021077 74.2540168324407 L 299.9550953313962 77.0849273144606 L 303.6147271525817 79.68630451415456 L 307.2743589737671 88.40856924254017 L 310.9339907949526 89.32670237184391 L 314.593622616138 92.23412394797246 L 318.2532544373235 100.42081101759754 L 321.91288625850893 101.49196633511858 L 325.5725180796944 110.67329762815606 L 329.23214990087985 112.96863045141546 L 332.8917817220653 115.7230298393267 L 336.5514135432508 121.53787299158378 L 340.21104536443625 126.81713848508033 L 343.8706771856217 130.18362662586074 L 347.5303090068071 133.16755929609795 L 351.18994082799264 134.69778117827084 L 354.84957264917807 137.9877582249426 L 358.50920447036356 138.90589135424636 L 362.16883629154904 141.8133129303749 L 365.8284681127345 143.34353481254783 L 369.48809993391995 144.03213465952564 L 373.1477317551053 145.33282325937262 L 376.80736357629087 144.87375669472073 L 380.4669953974763 146.55700076511093 L 384.1266272186618 147.24560061208877 L 387.7862590398472 148.54628921193572 L 391.4458908610327 148.08722264728385 L 395.1055226822182 148.3167559296098 L 398.76515450340366 149.3114001530222 L 402.4247863245891 149.38791124713083 L 406.0844181457746 149.92348890589136 L 409.7440499669599 149.54093343534814 L 413.4036817881454 149.3114001530

In [23]:
# show plot of TRUE vs. ESTIMATED rates
c, a, m = toyplot.scatterplot(
    partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0),         # estimated
    SPECIES_DATA['psi_x'],                             # true
    width=400,
    height=250,
    xlabel="ESTIMATED species velocity",
    ylabel="TRUE species velocity",
    color=[toyplot.color.Palette()[i] for i in SPECIES_DATA.gidx],
);

<svg class="toyplot-canvas-Canvas" height="250.0px" id="tb9f3f7fc07c84e2eb701e73b4019e331" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 400.0 250.0" width="400.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> -1 0 1 2 ESTIMATED species velocity -1 0 1 TRUE species velocity

In [50]:
stats.linregress(partpooled_model_partpooled_data['trace']['𝜓'].mean(axis=0), SPECIES_DATA['psi_x'])

LinregressResult(slope=0.8287773841647489, intercept=-0.24411975355049273, rvalue=0.9683185931218599, pvalue=9.31572260313291e-49, stderr=0.024200383380705164)

In [24]:
draw_velocity_dists(partpooled_model_partpooled_data['trace'], baseline = 1.8);

<svg class="toyplot-canvas-Canvas" height="300.0px" id="ta725211168c3484cbda0a6e6c2c13bb0" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" viewBox="0 0 350.0 300.0" width="350.0px" xmlns="http://www.w3.org/2000/svg" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink"> <polygon points="159.21388495145058,250.0 160.25007867835157,250.0 161.28627240525256,250.0 162.32246613215355,250.0 163.35865985905454,250.0 164.39485358595556,250.0 165.43104731285652,250.0 166.4672410397575,250.0 167.50343476665853,250.0 168.5396284935595,250.0 169.5758222204605,250.0 170.6120159473615,250.0 171.64820967426246,250.0 172.68440340116345,250.0 173.72059712806444,250.0 174.75679085496546,250.0 175.79298458186645,250.0 176.8291783087674,250.0 177.86537203566843,250.0 178.90156576256942,250.0 179.9377594894704,250.0 180.9739532163714,250.0 182.01014694327236,250.0 183.04634067017338,250.0 184.08253439707437,250.0 185.11872812397536,250.0 186.15492185087635,250.0 187.19111557777737,250.0 188.22730930467833,250.0 189.26350303157935,250.0 190.2996967584803,250.0 191.33589048538133,250.0 192.37208421228232,250.0 193.40827793918328,250.0 194.4444716660843,250.0 195.4806653929853,250.0 196.51685911988628,250.0 197.55305284678724,250.0 198.58924657368826,250.0 199.62544030058925,250.0 200.6616340274902,250.0 201.69782775439123,250.0 202.73402148129222,250.0 203.77021520819318,250.0 204.80640893509417,250.0 205.84260266199522,250.0 206.8787963888962,250.0 207.91499011579714,250.0 208.95118384269816,250.0 209.98737756959918,250.0 211.02357129650014,250.0 212.05976502340116,250.0 213.09595875030215,250.0 214.1321524772031,250.0 215.1683462041041,250.0 216.2045399310051,250.0 217.2407336579061,250.0 218.27692738480707,250.0 219.31312111170806,250.0 220.34931483860908,250.0 221.38550856551004,250.0 222.42170229241103,250.0 223.45789601931207,250.0 224.494089746213,250.0 225.530283473114,250.0 226.56647720001502,250.0 227.602670926916,250.0 228.638864653817,250.0 229.67505838071799,250.0 230.71125210761898,250.0 231.74744583451997,250.0 232.78363956142096,250.0 233.81983328832195,250.0 234.85602701522294,250.0 235.89222074212392,250.0 236.92841446902491,250.0 237.9646081959259,250.0 239.0008019228269,250.0 240.03699564972786,250.0 241.07318937662887,250.0 242.10938310352986,250.0 243.14557683043083,250.0 244.1817705573319,250.0 245.21796428423286,250.0 246.25415801113385,250.0 247.29035173803487,250.0 248.32654546493583,250.0 249.36273919183682,250.0 250.39893291873778,250.0 251.4351266456388,250.0 252.4713203725398,250.0 253.50751409944075,250.0 254.5437078263418,250.0 255.57990155324276,250.0 256.6160952801437,250.0 257.6522890070447,250.0 258.68848273394576,250.0 259.7246764608467,250.0 260.7608701877477,250.0 261.79706391464873,250.0 261.79706391464873,249.37250599717694 260.7608701877477,249.26541419747198 259.7246764608467,249.1428064579141 258.68848273394576,249.00294604679485 257.6522890070447,248.84398934187607 256.6160952801437,248.66399394703 255.57990155324276,248.4609298239901 254.5437078263418,248.23269368841997 253.50751409944075,247.97712687989466 252.4713203725398,247.6920368638463 251.4351266456388,247.37522245981998 250.39893291873778,247.02450281466443 249.36273919183682,246.63775005212526 248.32654546493583,246.21292543276974 247.29035173803487,245.74811875181672 246.25415801113385,245.24159058934018 245.21796428423286,244.69181691004326 244.1817705573319,244.09753539141656 243.14557683043083,243.45779274307765 242.10938310352986,242.77199217026288 241.07318937662887,242.03994003487483 240.03699564972786,241.26189068237315 239.0008019228269,240.43858833629764 237.9646081959259,239.5713049183357 236.92841446902491,238.66187263423086 235.89222074212392,237.71271017762692

### Assess model fit

In [165]:
def rmse(predictions, targets):
    differences = predictions - targets                       #the DIFFERENCEs.
    differences_squared = differences ** 2                    #the SQUAREs of ^
    mean_of_differences_squared = differences_squared.mean()  #the MEAN of ^
    rmse_val = np.sqrt(mean_of_differences_squared)           #ROOT of ^
    return rmse_val   

In [166]:
def aicm(mean, variance):
    return 2*mean - 2*variance

In [167]:
rmse(unpooled_sub['trace']['𝜓'].mean(axis=0), SPECIES_DATA['psi'])

0.9384409617057597

In [168]:
rmse(partpooled_sub['trace']['𝜓'].mean(axis=0), SPECIES_DATA['psi_x'])

0.6105422350829149

In [177]:
aicm(unpooled_sub['trace']['𝜓'].mean(), unpooled_sub['trace']['𝜓'].var())

-24.454868204001738

In [179]:
# Raftery et al. (2007) holds that this value is better.  R+M disagree?
aicm(partpooled_sub['trace']['𝜓'].mean(), partpooled_sub['trace']['𝜓'].var())

-12.49733802346165

In [39]:
az_pooled_model_pooled_data = az.from_pymc3(trace = pooled_model_pooled_data['trace'], 
                                            model = pooled_model_pooled_data['model'])
az_pooled_model_unpooled_data = az.from_pymc3(trace = pooled_model_unpooled_data['trace'], 
                                            model = pooled_model_unpooled_data['model'])
az_pooled_model_partpooled_data = az.from_pymc3(trace = pooled_model_partpooled_data['trace'], 
                                            model = pooled_model_partpooled_data['model'])
az_unpooled_model_pooled_data = az.from_pymc3(trace = unpooled_model_pooled_data['trace'], 
                                            model = unpooled_model_pooled_data['model'])
az_unpooled_model_unpooled_data = az.from_pymc3(trace = unpooled_model_unpooled_data['trace'], 
                                            model = unpooled_model_unpooled_data['model'])
az_unpooled_model_partpooled_data = az.from_pymc3(trace = unpooled_model_partpooled_data['trace'], 
                                            model = unpooled_model_partpooled_data['model'])
az_partpooled_model_pooled_data = az.from_pymc3(trace = partpooled_model_pooled_data['trace'], 
                                            model = partpooled_model_pooled_data['model'])
az_partpooled_model_unpooled_data = az.from_pymc3(trace = partpooled_model_unpooled_data['trace'], 
                                            model = partpooled_model_unpooled_data['model'])
az_partpooled_model_partpooled_data = az.from_pymc3(trace = partpooled_model_partpooled_data['trace'], 
                                            model = partpooled_model_partpooled_data['model'])

### Compare models with different datasets

In [40]:
az.compare({"pooled_model_pooled_data": az_pooled_model_pooled_data,
            "pooled_model_unpooled_data": az_pooled_model_unpooled_data, 
            "pooled_model_partpooled_data": az_pooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo    d_loo      weight  \
pooled_model_pooled_data        0 -550.222  1.97737        0    0.587556   
pooled_model_partpooled_data    1 -563.815  1.88354  13.5927    0.408613   
pooled_model_unpooled_data      2 -637.841  1.99272  87.6195  0.00383096   

                                   se      dse warning loo_scale  
pooled_model_pooled_data      27.2957        0   False       log  
pooled_model_partpooled_data  27.7087  37.2672   False       log  
pooled_model_unpooled_data    27.2933  36.8345   False       log

In [41]:
az.compare({"unpooled_model_pooled_data": az_unpooled_model_pooled_data,
            "unpooled_model_unpooled_data": az_unpooled_model_unpooled_data, 
            "unpooled_model_partpooled_data": az_unpooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo    d_loo      weight  \
unpooled_model_partpooled_data    0  -535.53  43.4493        0    0.648442   
unpooled_model_pooled_data        1 -550.696  10.7138  15.1663    0.349542   
unpooled_model_unpooled_data      2 -636.517  19.8555  100.987  0.00201584   

                                     se      dse warning loo_scale  
unpooled_model_partpooled_data  28.2077        0   False       log  
unpooled_model_pooled_data      26.4534   36.766   False       log  
unpooled_model_unpooled_data    26.4117  37.6298   False       log

In [42]:
az.compare({"partpooled_model_pooled_data": az_partpooled_model_pooled_data,
            "partpooled_model_unpooled_data": az_partpooled_model_unpooled_data, 
            "partpooled_model_partpooled_data": az_partpooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo    d_loo       weight  \
partpooled_model_partpooled_data    0 -521.206  22.5578        0     0.824814   
partpooled_model_pooled_data        1 -554.228  22.9155   33.022     0.175186   
partpooled_model_unpooled_data      2 -640.486   28.608  119.281  6.15858e-07   

                                       se      dse warning loo_scale  
partpooled_model_partpooled_data  29.2731        0   False       log  
partpooled_model_pooled_data      26.4576  36.8059   False       log  
partpooled_model_unpooled_data    28.1444  37.6351   False       log

### Compare datasets with different models

In [51]:
az.compare({"pooled_model_pooled_data": az_pooled_model_pooled_data,
            "unpooled_model_pooled_data": az_unpooled_model_pooled_data, 
            "partpooled_model_pooled_data": az_partpooled_model_pooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo     d_loo     weight  \
pooled_model_pooled_data        0 -550.222  1.97737         0   0.582894   
unpooled_model_pooled_data      1 -550.696  10.7138  0.474446   0.355826   
partpooled_model_pooled_data    2 -554.228  22.9155   4.00593  0.0612805   

                                   se       dse warning loo_scale  
pooled_model_pooled_data       26.463         0   False       log  
unpooled_model_pooled_data    26.5151  0.952563   False       log  
partpooled_model_pooled_data  26.9251   2.70981   False       log

In [52]:
az.compare({"pooled_model_unpooled_data": az_pooled_model_unpooled_data,
            "unpooled_model_unpooled_data": az_unpooled_model_unpooled_data, 
            "partpooled_model_unpooled_data": az_partpooled_model_unpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo    d_loo    weight  \
unpooled_model_unpooled_data      0 -636.517  19.8555        0  0.627322   
pooled_model_unpooled_data        1 -637.841  1.99272  1.32446  0.337165   
partpooled_model_unpooled_data    2 -640.486   28.608  3.96948  0.035513   

                                     se      dse warning loo_scale  
unpooled_model_unpooled_data    28.1206        0   False       log  
pooled_model_unpooled_data      28.0802  2.29206   False       log  
partpooled_model_unpooled_data  28.4247  1.47491   False       log

In [53]:
az.compare({"pooled_model_partpooled_data": az_pooled_model_partpooled_data,
            "unpooled_model_partpooled_data": az_unpooled_model_partpooled_data, 
            "partpooled_model_partpooled_data": az_partpooled_model_partpooled_data})

/home/henry/miniconda3/envs/py37/lib/python3.7/site-packages/arviz/stats/stats.py:150: UserWarning: 
The scale is now log by default. Use 'scale' argument or 'stats.ic_scale' rcParam if you rely on a specific value.
A higher log-score (or a lower deviance) indicates a model with better predictive accuracy.
  "\nThe scale is now log by default. Use 'scale' argument or "


rank      loo    p_loo    d_loo       weight  \
partpooled_model_partpooled_data    0 -521.206  22.5578        0      0.99481   
unpooled_model_partpooled_data      1  -535.53  43.4493  14.3243   0.00519016   
pooled_model_partpooled_data        2 -563.815  1.88354  42.6088  1.25625e-10   

                                       se      dse warning loo_scale  
partpooled_model_partpooled_data  27.4063        0   False       log  
unpooled_model_partpooled_data     26.799  5.33955   False       log  
pooled_model_partpooled_data      26.6598  10.0358   False       log

### other stuff

In [44]:
# Save trace.  To load in different notebook, model context and sample data is required.
pm.save_trace(partpooled_model_partpooled_data['trace'], directory = "/home/henry/oaks-thesis/trace/linear-pmpd")

'/home/henry/oaks-thesis/trace/linear-pmpd'

In [47]:
linear_args = [
    SAMPLE.dist,
    SAMPLE.RI_partpooled,
    SAMPLE.sidx0,
    SAMPLE.sidx1,
    gidx
]

In [48]:
# Magic command to move sample data across notebooks.   
%store linear_args

Stored 'linear_args' (list)
